In [1]:
import requests 
from bs4 import BeautifulSoup
import pandas as pd
import nltk
from nltk.stem import WordNetLemmatizer
import spacy
from spacy import displacy

In [2]:
url = "https://www.csis.org/analysis/toward-clean-and-secure-energy-future-indo-pacific-conversation-australian-minister"
response = requests.get(url)

In [3]:
soup=BeautifulSoup(response.content, "html.parser")

In [4]:
print(soup.prettify())

<!DOCTYPE html>
<html class="bg-blue-800" dir="ltr" lang="en" prefix="og: https://ogp.me/ns#">
 <head>
  <meta charset="utf-8"/>
  <meta content="CSIS Australia Chair hosted for a virtual conversation with Australian Minister for Climate Change and Energy Chris Bowen on Canberra's climate policy and opportunities for the U.S.-Australian partnership." name="description"/>
  <link href="https://www.csis.org/analysis/toward-clean-and-secure-energy-future-indo-pacific-conversation-australian-minister" rel="canonical"/>
  <link href="https://csis-website-prod.s3.amazonaws.com/s3fs-public/publication/GettyImages-543723408.jpg?VersionId=6YgfRY1JBrd4dfwAuMva6ZIpgWm_HYb2" rel="image_src"/>
  <meta content="Toward a Clean and Secure Energy Future in the Indo-Pacific: A Conversation with Australian Minister for Climate Change and Energy Chris Bowen" name="citation_title"/>
  <meta content="Fri, 09/23/2022 - 12:00" name="citation_publication_date"/>
  <meta content="Toward a Clean and Secure Energ

In [5]:
main_content = soup.find('div', {'class': 'wysiwyg-wrapper'})

In [6]:
text_list = []

In [7]:
start_collecting = False
end_text = "(END)"

In [8]:
for paragraph in content_div.find_all('p'):
    paragraph_text = paragraph.get_text(separator=' ', strip=True)
    
    if end_text in paragraph_text:
        text_list.append(paragraph_text)
        break

    if "Charles Edel" in paragraph_text:
        start_collecting = True

    if start_collecting:
        text_list.append(paragraph_text)

In [9]:
df = pd.DataFrame(text_list, columns=["Paragraph Text"])
df.to_csv('03_paragraphs.csv', index=False)

In [10]:
df

Paragraph Text
0    Charles Edel: Good afternoon to our audience w...
1    Today we were lucky enough to host here at CSI...
2    Now I’m very excited to say that concluding th...
3    But if the timing is auspicious, it’s also cri...
4    The Honorable Chris Bowen is, as I said, minis...
..                                                 ...
122                 Dr. Edel: Well, safe travels home.
123                            Min. Bowen: Good on ya!
124                               Dr. Edel: Thank you.
125                    Min. Bowen: Cheers. (Applause.)
126                                              (END)

[127 rows x 1 columns]

In [11]:
pip install nltk

Note: you may need to restart the kernel to use updated packages.


In [12]:
nltk.download('punkt')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /Users/loogyee/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /Users/loogyee/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [13]:
nlp = spacy.load("en_core_web_sm")

In [14]:
df = pd.read_csv('03_paragraphs.csv')

In [15]:
# Preprocessing 
lemmatizer = WordNetLemmatizer()

def preprocess_text(text):
    # Lowercase the entire text
    text = text.lower()
    
    # Tokenize and lemmatize
    lemmatized_words = []
    for word in text.split():  # Split the text into words
        lemmatized_words.append(lemmatizer.lemmatize(word))  # Lemmatize each word
    
    # Join lemmatized words back into a single string
    cleaned_text = ' '.join(lemmatized_words)
    
    return cleaned_text

In [16]:
df['Processed Text'] = df['Paragraph Text'].apply(preprocess_text)

In [17]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


In [18]:
pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-3.6.0/en_core_web_sm-3.6.0.tar.gz

  Using cached https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-3.6.0/en_core_web_sm-3.6.0.tar.gz (12.8 MB)
  Preparing metadata (setup.py) ... done
Note: you may need to restart the kernel to use updated packages.


In [19]:
relationship_keywords = {'collaboration', 'cooperation', 'partner', 'engage', 
                         'support', 'fund', 'finance', 'invest', 'develop', 
                         'supply', 'promote', 'transition', 'export', 'agreement', 
                         'interest', 'share', 'enhance', 'effort', 'import'}

In [20]:
def extract_entities_and_relationships(text):
    doc = nlp(text)  # Process text with spaCy
    entities = [(ent.text, ent.label_) for ent in doc.ents if ent.label_ in ['ORG', 'GPE']]  # Extract only ORG and GPE entities

    # Find relationships based on keywords
    relationships = []
    for token in doc:
        if token.text in relationship_keywords:  # Check if the token matches any relationship keyword
            subject = [w for w in token.children if w.dep_ == "nsubj"]  # Find the subject
            object_ = [w for w in token.children if w.dep_ == "dobj"]  # Find the direct object
            if subject and object_:
                relationships.append((subject[0].text, token.text, object_[0].text))  # (subject, relationship keyword, object)

    return entities, relationships

In [21]:
df['Entities'], df['Relationships'] = zip(*df['Processed Text'].apply(extract_entities_and_relationships))

In [22]:
df[['Processed Text', 'Entities', 'Relationships']]

Processed Text  \
0    charles edel: good afternoon to our audience w...   
1    today we were lucky enough to host here at csi...   
2    now i’m very excited to say that concluding th...   
3    but if the timing is auspicious, it’s also cri...   
4    the honorable chris bowen is, a i said, minist...   
..                                                 ...   
122                  dr. edel: well, safe travel home.   
123                            min. bowen: good on ya!   
124                               dr. edel: thank you.   
125                    min. bowen: cheers. (applause.)   
126                                              (end)   

                                              Entities Relationships  
0    [(the australia chair, ORG), (the australia ch...            []  
1                                  [(washington, GPE)]            []  
2    [(the united state, ORG), (pittsburgh, GPE), (...            []  
3                                   [(australia, GPE)]            []  
4                   [(mcmahon, ORG), (fairfield, GPE)]            []  
..                                                 ...           ...  
122                                                 []            []  
123                                                 []            []  
124                                                 []            []  
125                                                 []            []  
126                                                 []            []  

[127 rows x 3 columns]

In [23]:
for index, row in df.iterrows():
    print(f"\nParagraph {index + 1}:")
    print(row['Paragraph Text'])

    # Display dependency parsing
    doc = nlp(row['Processed Text'])
    sentence_spans = list(doc.sents)
    displacy.render(sentence_spans, style='dep', jupyter=True, options={'compact': True})
    
    # Display named entities
    displacy.render(sentence_spans, style="ent", jupyter=True)

    # Print extracted entities and relationships
    print("Entities:", row['Entities'])


Paragraph 1:
Charles Edel: Good afternoon to our audience who is tuning in online to watch this, as well to those who are here today at CSIS. I’m Charles Edel, the Australia Chair and senior advisor here at the Center for Strategic and International Studies. The Australia Chair, which was generously endowed by Pratt Industries, is dedicated to increasing mutual understanding between the United States and Australia and serving as an independent platform to pursue policies that help advance, deepen, and broaden the bilateral alliance.


Entities: [('the australia chair', 'ORG'), ('the australia chair', 'ORG'), ('pratt industries', 'ORG'), ('the united state', 'ORG'), ('australia', 'GPE')]

Paragraph 2:
Today we were lucky enough to host here at CSIS our first American Australian Indo-Pacific Strategic Dialogue. The conference brought together key stakeholders, decisionmakers, and strategic thinkers from both countries as we pursued ideas to advance both how Washington and Canberra can work together to facilitate a more prosperous and more secure future for both of us. I want to sincerely thank all of our conference participants for participating, many of whom are in the room with us. And your thoughtful comments really helped us in thinking about what are the future moves that we need to pursue together.


/Users/loogyee/anaconda3/lib/python3.11/site-packages/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


Entities: [('washington', 'GPE')]

Paragraph 3:
Now I’m very excited to say that concluding this conference it’s my great pleasure to welcome the honorable Christopher Bowen, who is making his first trip to the United States in his new role as minister for climate change and energy. Minister Bowen is here, having just flown in from Pittsburgh, where he participated on the Global Clean Energy Action Forum. The timing for today’s conversation on securing a clean and secure energy future for the Indo-Pacific is auspicious, as both Australia and the United States have recently passed major climate legislation.


Entities: [('the united state', 'ORG'), ('pittsburgh', 'GPE'), ('australia', 'GPE'), ('the united state', 'ORG')]

Paragraph 4:
But if the timing is auspicious, it’s also critical given what’s at stake for both of our countries, for the region and, indeed, for our entire planet. To that end, Australia’s new government is moving climate policy to center stage in both how it approaches its domestic and its foreign policies. We’re delighted to host Mr. Bowen here at CSIS today, who will lay out how the new Australian government plans on doing just that.


...

Entities: []

Paragraph 124:
Min. Bowen: Good on ya!


Entities: []

Paragraph 125:
Dr. Edel: Thank you.


Entities: []

Paragraph 126:
Min. Bowen: Cheers. (Applause.)


Entities: []

Paragraph 127:
(END)


Entities: []


In [24]:
entity1_list = []
relationship_list = []
entity2_list = []
date_list = []
money_list = []

In [25]:
# Iterate through each paragraph
for index, row in df.iterrows():
    doc = nlp(row['Paragraph Text'])  # Process the paragraph with spaCy

    for sent in doc.sents:
        # Extract named entities (countries, organizations)
        entities = []
        money_in_sentence = []

        for ent in sent.ents:
            if ent.label_ == 'Initiative' in ent.text:
                entities.append(ent._replace(label_='POL'))  # Change label for specific case
            elif ent.label_ in ['GPE', 'ORG', 'POL', 'MONEY']:
                entities.append(ent)

            # Collect monetary amounts
            if ent.label_ == "MONEY":
                money_in_sentence.append(ent.text)
        
        # Look for verbs or specific relationship nouns in the sentence
        verbs = [token for token in sent if token.pos_ == "VERB"]
        keywords_in_sentence = [token.text for token in sent if token.lemma_ in relationship_keywords]
        
        # Extract dates
        dates = [ent.text for ent in sent.ents if ent.label_ == "DATE"]

        # If we find two entities and a relationship keyword, we assume a relationship
        if len(entities) >= 2 and keywords_in_sentence:
            entity1_list.append(entities[0].text)

            # Concatenate the relationship noun and verb (if available) into one string
            relationship_info = keywords_in_sentence[0]
            if verbs:
                relationship_info += " (verb: " + verbs[0].lemma_ + ")"

            relationship_list.append(relationship_info)  # Store concatenated info
            entity2_list.append(entities[1].text)
            date_list.append(dates[0] if dates else "n/a")
            money_list.append(money_in_sentence[0] if money_in_sentence else "n/a")

In [26]:
# DataFrame
extracted_data = pd.DataFrame({
    "Entity1": entity1_list,
    "Relationship": relationship_list,
    "Entity2": entity2_list,
    "Date": date_list,
    "Money": money_list
})

In [27]:
extracted_data

Entity1                Relationship  \
0                             COVID-19       supply (verb: expose)   
1                              Ukraine         supply (verb: have)   
2                               Amanda         supply (verb: know)   
3                                Japan     supporting (verb: play)   
4                            Australia        supply (verb: think)   
5                              America          interest (verb: ’)   
6                            Australia         invested (verb: ’m)   
7                            Australia         share (verb: share)   
8   the Clean Energy Demand Initiative         shared (verb: sign)   
9   The Clean Energy Demand Initiative    partner (verb: increase)   
10                               Apple         interest (verb: ’m)   
11                               Japan       partners (verb: work)   
12                           Indonesia        support (verb: hold)   
13                           Australia       partner (verb: think)   
14                           Australia      transition (verb: say)   
15                             Cabinet      engaged (verb: engage)   
16                                 COP         engage (verb: hope)   
17                           Indonesia  agreements (verb: discuss)   
18                           Australia          partner (verb: ’m)   

                Entity2       Date                Money  
0                Russia        n/a                  n/a  
1                Russia        n/a                  n/a  
2                    EV        n/a                  n/a  
3     the United States        n/a                  n/a  
4     the United States        n/a                  n/a  
5             Australia        n/a                  n/a  
6   billions of dollars        n/a  billions of dollars  
7                  U.S.        n/a                  n/a  
8            Pittsburgh  This week                  n/a  
9             Australia        n/a                  n/a  
10    Johnson & Johnson        n/a   up to $2.9 billion  
11                Korea        n/a                  n/a  
12            Australia     annual                  n/a  
13    the United States        n/a                  n/a  
14            Australia       2050                  n/a  
15             New York        n/a                  n/a  
16                  COP        n/a                  n/a  
17             Malaysia        n/a                  n/a  
18            Indonesia        n/a                  n/a

In [29]:
# Export to csv
extracted_data.to_csv('03_relationship.csv', index=False)